In [101]:
#Imports and API Key
#building in offsets

#Imports and API Key

import pandas as pd
import quandl
from scipy import stats
import scipy
from sklearn.linear_model import LogisticRegression, LinearRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import log_loss
import matplotlib.pyplot as plt
from sklearn.metrics import roc_auc_score

import numpy as np
import sys

from sklearn.pipeline import Pipeline

from basis_expansions.basis_expansions import (
    Polynomial, LinearSpline)

from regression_tools.dftransformers import (
    ColumnSelector, Identity, FeatureUnion, MapFeature, Intercept)

from sklearn.preprocessing import StandardScaler

from sklearn.linear_model import Ridge
from sklearn.linear_model import RidgeClassifier

import xgboost as xgb

%aimport dataclean

quandl.ApiConfig.api_key = 'm8FYMyoCaJSbTrBASNHh'

In [102]:
#pulling data from Quandl

data = pd.read_csv('datasources2.csv') #staging the QUANDL keys to pull in CSV
cols = list(data['Var_name'].astype('str'))
dataset = quandl.get([val for val in data['Quandl Key']]) #looping through the QUANDL keys to pull it into one DF
dataset.columns = cols

In [103]:
#pulling FED Yield Curve data

yields = pd.read_csv('Fed10Y_3M.csv')
yields['Date'] = pd.to_datetime(yields['Date'])
yields['Date'] = yields['Date'].apply(lambda x: x.strftime('%Y-%m'))
yields = yields.set_index('Date')
yields = yields.drop(['3 Month Treasury Yield', 'Rec_prob', 'NBER_Rec','Unnamed: 7'], axis=1) 

In [104]:
#need to write in special logic to factor in for 3YRT being a daily

treas = dataset['3YRT']
dataset = dataset.drop(columns = ['3YRT'])

In [105]:
treas = treas.resample('MS').mean()

In [106]:
## back to working on the general data
dataset.index = dataset.index.strftime('%Y-%m') #converting the datetime index to Y/M so it is collapsable
dataset = dataset.groupby(dataset.index, as_index=True).agg(sum) #collapsing by Y/M

In [107]:
#readd 3YRT back into data

dataset = dataset.join(treas, how='outer')

In [108]:
#converting GDP quarterly data into monthly - need to convert it so it fills in the following 3 months

dataset = dataclean.convert_q_to_m(dataset, 'GDP')

#converting consumer sentiment into monthly

dataset = dataclean.convert_q_to_m(dataset, 'CONS_SENT')

In [109]:
offset_dict = {'PMI':1, 'UNR':1, 'YUNR':1,'US_NHOME_SALES':1, 'PART_TIME':1, 'CPPR_PRICE':1, 'HOUS_PERMS':1, 'HOUS_STARTS':1, 'CAP_UTIL':1, 'PERS_SAVINGS':3, 'EXPORTS':3, 'IMPORTS':3, 'TRADE_BALANCE':3, 'US_M2':1, 'US_NHOME_SALES':1,'PPI':1,'CPI':1} #positives shift down, negatives shift up. Goal of this dict is to align data to when it gets released

In [110]:
for entry in offset_dict:
    #print(entry)
    #print(offset_dict[entry])
    dataset[str(entry)] = dataset[str(entry)].shift(offset_dict[entry])

In [111]:
#calculating change in GDP and converting Y into categorical values 
dataset['Recession'] = ((dataset['GDP'] - dataset['GDP'].shift(3)) < 0).astype(int)
#dataset = dataset.drop(columns = ['GDP','Recession']) #dropping calc column and recession column from dataset, experimenting with taking out fed funds rate

In [112]:
#merge fed interest rate data here
dataset = dataset.join(yields, how='outer')

In [113]:
dataset.shape

(1286, 24)

In [114]:
dataset = dataset[552:]

In [115]:
dataset = dataset[:-12]

In [116]:
#substituting mean value in for missing values and adding dummy column to indicate where done

for col in dataset.columns:
    if str(col)=='Recession':
        continue
    dataclean.clean_zeros(col, dataset)

In [117]:
dataset['3YRT'] = dataset['3YRT'].fillna(dataset['3YRT'].mean())

In [118]:
dataset.head()

PMI  UNR  YUNR  CONS_SENT  PART_TIME  CPPR_PRICE   HOUS_PERMS  \
1959-01-01  60.5  6.2  12.1       90.8     1081.0  165.088781  1331.221607   
1959-02-01  64.4  6.0  11.6       90.8     1022.0  165.088781  1331.221607   
1959-03-01  66.9  5.9  11.1       90.8      973.0  165.088781  1331.221607   
1959-04-01  67.1  5.6  11.1       90.8     1102.0  165.088781  1331.221607   
1959-05-01  66.9  5.2  10.8       95.3     1086.0  165.088781  1331.221607   

            HOUS_STARTS   CAP_UTIL  PERS_SAVINGS  EXPORTS  IMPORTS  \
1959-01-01  1429.531856  69.480123      8.779086   1349.0   1091.0   
1959-02-01  1657.000000  69.480123      8.779086   1401.0   1156.0   
1959-03-01  1667.000000  69.480123      8.779086   1339.0   1139.0   
1959-04-01  1620.000000  69.480123     11.300000   1314.0   1166.0   
1959-05-01  1590.000000  69.480123     10.600000   1256.0   1202.0   

            TRADE_BALANCE  INT_RATE      US_M2  US_NHOME_SALES   PPI  \
1959-01-01          258.0      2.48  4028.7241      606.030471  31.6   
1959-02-01          245.0      2.43   286.6000      606.030471  31.7   
1959-03-01          200.0      2.80   287.7000      606.030471  31.7   
1959-04-01          148.0      2.96   289.2000      606.030471  31.7   
1959-05-01           54.0      2.90   290.1000      606.030471  31.8   

                  CPI       GDP      3YRT  Recession  10 Year Treasury Yield  \
1959-01-01  13.253507  3121.936  5.572142        0.0                    4.02   
1959-02-01  13.299366  3121.936  5.572142        0.0                    3.96   
1959-03-01  13.253507  3121.936  5.572142        0.0                    3.99   
1959-04-01  13.253507  3192.380  5.572142        0.0                    4.12   
1959-05-01  13.299366  3192.380  5.572142        0.0                    4.31   

            3 Month Treasury Yield (Bond Equivalent Basis)  Spread  \
1959-01-01                                            2.88    1.14   
1959-02-01                                            2.76    1.20   
1959-03-01                                            2.86    1.13   
1959-04-01                                            3.01    1.11   
1959-05-01                                            2.90    1.41   

            CPPR_PRICE_PXY  HOUS_PERMS_PXY  HOUS_STARTS_PXY  CAP_UTIL_PXY  \
1959-01-01               1               1                1             1   
1959-02-01               1               1                0             1   
1959-03-01               1               1                0             1   
1959-04-01               1               1                0             1   
1959-05-01               1               1                0             1   

            PERS_SAVINGS_PXY  US_M2_PXY  US_NHOME_SALES_PXY  CPI_PXY  
1959-01-01                 1          1                   1        0  
1959-02-01                 1          0                   1        0  
1959-03-01                 1          0                   1        0  
1959-04-01                 0          0                   1        0  
1959-05-01                 0          0                   1        0

In [119]:
#adding momentum factors

momentum_cols = list(dataset.columns[:-6])

momentum_cols.remove('PPI') #removing PPI and CPI because they need a different transformation
momentum_cols.remove('CPI')
momentum_cols.remove('Recession')

for i in [1,3,12]:
    for col in momentum_cols:
        dataclean.create_momentum(col,dataset,i)

In [120]:
#CPI Calcs

for i in [1,3,12]:
    for col in ['CPI','PPI']:
        dataclean.infl_momentum(col,dataset,i)

In [121]:
pd.set_option('display.max_columns', None)
dataset.head()

PMI  UNR  YUNR  CONS_SENT  PART_TIME  CPPR_PRICE   HOUS_PERMS  \
1959-01-01  60.5  6.2  12.1       90.8     1081.0  165.088781  1331.221607   
1959-02-01  64.4  6.0  11.6       90.8     1022.0  165.088781  1331.221607   
1959-03-01  66.9  5.9  11.1       90.8      973.0  165.088781  1331.221607   
1959-04-01  67.1  5.6  11.1       90.8     1102.0  165.088781  1331.221607   
1959-05-01  66.9  5.2  10.8       95.3     1086.0  165.088781  1331.221607   

            HOUS_STARTS   CAP_UTIL  PERS_SAVINGS  EXPORTS  IMPORTS  \
1959-01-01  1429.531856  69.480123      8.779086   1349.0   1091.0   
1959-02-01  1657.000000  69.480123      8.779086   1401.0   1156.0   
1959-03-01  1667.000000  69.480123      8.779086   1339.0   1139.0   
1959-04-01  1620.000000  69.480123     11.300000   1314.0   1166.0   
1959-05-01  1590.000000  69.480123     10.600000   1256.0   1202.0   

            TRADE_BALANCE  INT_RATE      US_M2  US_NHOME_SALES   PPI  \
1959-01-01          258.0      2.48  4028.7241      606.030471  31.6   
1959-02-01          245.0      2.43   286.6000      606.030471  31.7   
1959-03-01          200.0      2.80   287.7000      606.030471  31.7   
1959-04-01          148.0      2.96   289.2000      606.030471  31.7   
1959-05-01           54.0      2.90   290.1000      606.030471  31.8   

                  CPI       GDP      3YRT  Recession  10 Year Treasury Yield  \
1959-01-01  13.253507  3121.936  5.572142        0.0                    4.02   
1959-02-01  13.299366  3121.936  5.572142        0.0                    3.96   
1959-03-01  13.253507  3121.936  5.572142        0.0                    3.99   
1959-04-01  13.253507  3192.380  5.572142        0.0                    4.12   
1959-05-01  13.299366  3192.380  5.572142        0.0                    4.31   

            3 Month Treasury Yield (Bond Equivalent Basis)  Spread  \
1959-01-01                                            2.88    1.14   
1959-02-01                                            2.76    1.20   
1959-03-01                                            2.86    1.13   
1959-04-01                                            3.01    1.11   
1959-05-01                                            2.90    1.41   

            CPPR_PRICE_PXY  HOUS_PERMS_PXY  HOUS_STARTS_PXY  CAP_UTIL_PXY  \
1959-01-01               1               1                1             1   
1959-02-01               1               1                0             1   
1959-03-01               1               1                0             1   
1959-04-01               1               1                0             1   
1959-05-01               1               1                0             1   

            PERS_SAVINGS_PXY  US_M2_PXY  US_NHOME_SALES_PXY  CPI_PXY  \
1959-01-01                 1          1                   1        0   
1959-02-01                 1          0                   1        0   
1959-03-01                 1          0                   1        0   
1959-04-01                 0          0                   1        0   
1959-05-01                 0          0                   1        0   

            PMI_1m_shift  UNR_1m_shift  YUNR_1m_shift  CONS_SENT_1m_shift  \
1959-01-01           NaN           NaN            NaN                 NaN   
1959-02-01           3.9          -0.2           -0.5                 0.0   
1959-03-01           2.5          -0.1           -0.5                 0.0   
1959-04-01           0.2          -0.3            0.0                 0.0   
1959-05-01          -0.2          -0.4           -0.3                 4.5   

            PART_TIME_1m_shift  CPPR_PRICE_1m_shift  HOUS_PERMS_1m_shift  \
1959-01-01                 NaN                  NaN                  NaN   
1959-02-01               -59.0                  0.0                  0.0   
1959-03-01               -49.0                  0.0                  0.0   
1959-04-01               129.0                  0.0                  0.0   
1959-05-01               -16.0                  0

In [126]:
#spline time - splines seriously impede the model, Time Horizon of 1 goes from LL of 4.9 to 8.19, AUC degreades by .04
#stickiness remains

#individual splines

PMI_fit = Pipeline([
    ('PMI', ColumnSelector(name='PMI')),
    ('PMI_spline', LinearSpline(knots=[44,45,47,48]))
])

CONS_SENT_fit = Pipeline([
    ('CONS_SENT', ColumnSelector(name='CONS_SENT')),
    ('CONS_SENT_spline', LinearSpline(knots=[64,68,72,75]))
])

INT_RATE_fit = Pipeline([
    ('INT_RATE', ColumnSelector(name='INT_RATE')),
    ('INT_RATE_spline', LinearSpline(knots=[8.75]))
])

US_NHOME_SALES_fit = Pipeline([
    ('US_NHOME_SALES', ColumnSelector(name='US_NHOME_SALES')),
    ('US_NHOME_SALES_spline', LinearSpline(knots=[450,475,500]))
])

THREE_YRT_fit = Pipeline([
    ('3YRT', ColumnSelector(name='3YRT')),
    ('3YRT_spline', LinearSpline(knots=[11.5]))
])

Spread_fit = Pipeline([
    ('Spread', ColumnSelector(name='Spread')),
    ('Spread_spline', LinearSpline(knots=[-0.1]))
])

CONS_SENT_1m_shift_fit = Pipeline([
    ('CONS_SENT_1m_shift', ColumnSelector(name='CONS_SENT_1m_shift')),
    ('CONS_SENT_1m_shift_spline', LinearSpline(knots=[-5]))
])


CAP_UTIL_1m_shift_fit = Pipeline([
    ('CAP_UTIL_1m_shift', ColumnSelector(name='CAP_UTIL_1m_shift')),
    ('CAP_UTIL_1m_shift_spline', LinearSpline(knots=[-0.5,-0.35,-0.25]))
])

THREE_YRT_1m_shift_fit = Pipeline([
    ('3YRT_1m_shift', ColumnSelector(name='3 YRT_1m_shift')),
    ('3YRT_1m_shift_spline', LinearSpline(knots=[-0.48,-0.46]))
])

THREE_MTREAS_YIELD_1m_shift_fit = Pipeline([
    ('3 Month Treasury Yield (Bond Equivalent Basis)_1m_shift', ColumnSelector(name='3 Month Treasury Yield (Bond Equivalent Basis)_1m_shift')),
    ('3 Month Treasury Yield (Bond Equivalent Basis)_1m_shift_spline', LinearSpline(knots=[-0.625,-0.45]))
])

PMI_3m_shift_fit = Pipeline([
    ('PMI_3m_shift', ColumnSelector(name='PMI_3m_shift')),
    ('PMI_3m_shift_spline', LinearSpline(knots=[-6.5,-5.5,-5.25,-3]))
])

UNR_3m_shift_fit = Pipeline([
    ('UNR_3m_shift', ColumnSelector(name='UNR_3m_shift')),
    ('UNR_3m_shift_spline', LinearSpline(knots=[0.1,0.4]))
])

YUNR_3m_shift_fit = Pipeline([
    ('YUNR_3M_SHIFT', ColumnSelector(name='YUNR_3m_shift')),
    ('YUNR_3M_SHIFT_spline', LinearSpline(knots=[0.5,1]))
])

CONS_SENT_3m_shift_fit = Pipeline([
    ('CONS_SENT_3m_shift', ColumnSelector(name='CONS_SENT_3m_shift')),
    ('CONS_SENT_3m_shift_spline', LinearSpline(knots=[-7,-4.5]))
])

CAP_UTIL_3m_shift_fit = Pipeline([
    ('CAP_UTIL_3m_shift', ColumnSelector(name='CAP_UTIL_3m_shift')),
    ('CAP_UTIL_3m_shift_spline', LinearSpline(knots=[-1.6,-1.5,-1,-0.9]))
])

THREE_MTREAS_YIELD_3m_shift_fit = Pipeline([
    ('3 Month Treasury Yield (Bond Equivalent Basis)_3m_shift', ColumnSelector(name='3 Month Treasury Yield (Bond Equivalent Basis)_3m_shift')),
    ('3 Month Treasury Yield (Bond Equivalent Basis)_3m_shift_spline', LinearSpline(knots=[-1.4]))
])

UNR_12m_shift_fit = Pipeline([
    ('UNR_12m_shift', ColumnSelector(name='UNR_12m_shift')),
    ('UNR_12m_shift_spline', LinearSpline(knots=[2.5,3]))
])

CONS_SENT_12m_shift_fit = Pipeline([
    ('CONS_SENT_12m_shift', ColumnSelector(name='CONS_SENT_12m_shift')),
    ('CONS_SENT_12m_shift_spline', LinearSpline(knots=[-15,-12,-11]))
])

HOUS_PERMS_12m_shift_fit = Pipeline([
    ('HOUS_PERMS_12m_shift', ColumnSelector(name='HOUS_PERMS_12m_shift')),
    ('HOUS_PERMS_12m_shift_spline', LinearSpline(knots=[-375,-300,-200]))
])

HOUS_STARTS_12m_shift_fit = Pipeline([
    ('HOUS_STARTS_12m_shift', ColumnSelector(name='HOUS_STARTS_12m_shift')),
    ('HOUS_STARTS_12m_shift_spline', LinearSpline(knots=[-375,-300]))
])

THREE_YRT_12m_shift_fit = Pipeline([
    ('THREE_YRT_12m_shift', ColumnSelector(name='3YRT_12m_shift')),
    ('THREE_YRT_12m_shift_spline', LinearSpline(knots=[1.75]))
])

TEN_YRT_YIELD_12m_shift_fit = Pipeline([
    ('TEN_YRT_YIELD_12m_shift', ColumnSelector(name='10 Year Treasury Yield_12m_shift')),
    ('10 Year Treasury Yield_12m_shift_spline', LinearSpline(knots=[1.2,1.6]))
])

Spread_12m_shift_fit = Pipeline([
    ('Spread_12m_shift', ColumnSelector(name='Spread_12m_shift')),
    ('Spread_12m_shift_spline', LinearSpline(knots=[1,1.1]))
])

PPI_1m_shift_fit = Pipeline([
    ('PPI_1m_shift', ColumnSelector(name='PPI_1m_shift')),
    ('PPI_1m_shift_spline', LinearSpline(knots=[1.3]))
])

CPI_1m_shift_fit = Pipeline([
    ('CPI_1m_shift', ColumnSelector(name='CPI_1m_shift')),
    ('CPI_1m_shift_spline', LinearSpline(knots=[1.8]))
])

PPI_3m_shift_fit = Pipeline([
    ('PPI_3m_shift', ColumnSelector(name='PPI_3m_shift')),
    ('PPI_3m_shift_spline', LinearSpline(knots=[2.75,3,3.25,3.35]))
])

CPI_12m_shift_fit = Pipeline([
    ('CPI_12m_shift', ColumnSelector(name='CPI_12m_shift')),
    ('CPI_12m_shift_spline', LinearSpline(knots=[5.5]))
])

PPI_12m_shift_fit = Pipeline([
    ('PPI_12m_shift', ColumnSelector(name='PPI_12m_shift')),
    ('PPI_12m_shift_spline', LinearSpline(knots=[14]))
])


#union features together

feature_pipeline = FeatureUnion([
    ('intercept', Intercept()),
    ('PMI', PMI_fit),
    ('CONS_SENT', CONS_SENT_fit),
    ('INT_RATE', INT_RATE_fit),
    ('US_NHOME_SALES', US_NHOME_SALES_fit),
    ('THREE_YRT', THREE_YRT_fit),
    ('Spread', Spread_fit),
    ('CONS_SENT_1m_shift', CONS_SENT_1m_shift_fit),
    ('CAP_UTIL_1m_shift', CAP_UTIL_1m_shift_fit),
    ('THREE_MTREAS_YIELD_1m_shift', THREE_MTREAS_YIELD_1m_shift_fit),
    ('PMI_3m_shift', PMI_3m_shift_fit),
    ('UNR_3m_shift', UNR_3m_shift_fit),
    ('YUNR_3M_SHIFT', YUNR_3m_shift_fit),
    ('CONS_SENT_3m_shift', CONS_SENT_3m_shift_fit),
    ('CAP_UTIL_3m_shift', CAP_UTIL_3m_shift_fit),
    ('3 Month Treasury Yield_3m_shift', THREE_MTREAS_YIELD_3m_shift_fit),
    ('UNR_12m_shift', UNR_12m_shift_fit),
    ('CONS_SENT_12m_shift', CONS_SENT_12m_shift_fit),
    ('HOUS_PERMS_12m_shift', HOUS_PERMS_12m_shift_fit),
    ('HOUS_STARTS_12m_shift', HOUS_STARTS_12m_shift_fit), 
    ('THREE_YRT_12m_shift', THREE_YRT_12m_shift_fit),
    ('TEN_YRT_YIELD_12m_shift', TEN_YRT_YIELD_12m_shift_fit),
    ('Spread_12m_shift', Spread_12m_shift_fit),
    ('PPI_1m_shift', PPI_1m_shift_fit),
    ('CPI_1m_shift', CPI_1m_shift_fit),
    ('PPI_3m_shift', PPI_3m_shift_fit),
    ('CPI_12m_shift', CPI_12m_shift_fit),
    ('PPI_12m_shift', PPI_12m_shift_fit)
    ])


feature_pipeline.fit(dataset)
features = feature_pipeline.transform(dataset)

In [127]:
features.head()

intercept  PMI_spline_linear  PMI_spline_0  PMI_spline_1  \
1959-01-01        1.0               60.5          16.5          15.5   
1959-02-01        1.0               64.4          20.4          19.4   
1959-03-01        1.0               66.9          22.9          21.9   
1959-04-01        1.0               67.1          23.1          22.1   
1959-05-01        1.0               66.9          22.9          21.9   

            PMI_spline_2  PMI_spline_3  CONS_SENT_spline_linear  \
1959-01-01          13.5          12.5                     90.8   
1959-02-01          17.4          16.4                     90.8   
1959-03-01          19.9          18.9                     90.8   
1959-04-01          20.1          19.1                     90.8   
1959-05-01          19.9          18.9                     95.3   

            CONS_SENT_spline_0  CONS_SENT_spline_1  CONS_SENT_spline_2  \
1959-01-01                26.8                22.8                18.8   
1959-02-01                26.8                22.8                18.8   
1959-03-01                26.8                22.8                18.8   
1959-04-01                26.8                22.8                18.8   
1959-05-01                31.3                27.3                23.3   

            CONS_SENT_spline_3  INT_RATE_spline_linear  INT_RATE_spline_0  \
1959-01-01                15.8                    2.48                0.0   
1959-02-01                15.8                    2.43                0.0   
1959-03-01                15.8                    2.80                0.0   
1959-04-01                15.8                    2.96                0.0   
1959-05-01                20.3                    2.90                0.0   

            US_NHOME_SALES_spline_linear  US_NHOME_SALES_spline_0  \
1959-01-01                    606.030471               156.030471   
1959-02-01                    606.030471               156.030471   
1959-03-01                    606.030471               156.030471   
1959-04-01                    606.030471               156.030471   
1959-05-01                    606.030471               156.030471   

            US_NHOME_SALES_spline_1  US_NHOME_SALES_spline_2  \
1959-01-01               131.030471               106.030471   
1959-02-01               131.030471               106.030471   
1959-03-01               131.030471               106.030471   
1959-04-01               131.030471               106.030471   
1959-05-01               131.030471               106.030471   

            3YRT_spline_linear  3YRT_spline_0  Spread_spline_linear  \
1959-01-01            5.572142            0.0                  1.14   
1959-02-01            5.572142            0.0                  1.20   
1959-03-01            5.572142            0.0                  1.13   
1959-04-01            5.572142            0.0                  1.11   
1959-05-01            5.572142            0.0                  1.41   

            Spread_spline_0  CONS_SENT_1m_shift_spline_linear  \
1959-01-01             1.24                               NaN   
1959-02-01             1.30                               0.0   
1959-03-01             1.23                               0.0   
1959-04-01             1.21                               0.0   
1959-05-01             1.51                               4.5   

            CONS_SENT_1m_shift_spline_0  CAP_UTIL_1m_shift_spline_linear  \
1959-01-01                          NaN                              NaN   
1959-02-01                          5.0                              0.0   
1959-03-01                          5.0                              0.0   
1959-04-01                          5.0                              0.0   
1959-05-01                          9.5                              0.0   

            CAP_UTIL_1m_shift_spline_0  CAP_UTIL_1m_shift_spline_1  \
1959-01-01                         NaN                         NaN   
1959-02-01                         0.5               

In [128]:
#dropping columns from OG dataset that were splined

splined_cols = ['PMI','CONS_SENT','INT_RATE','US_NHOME_SALES','3YRT','Spread','CONS_SENT_1m_shift','CAP_UTIL_1m_shift',
                '3YRT_1m_shift', '3 Month Treasury Yield (Bond Equivalent Basis)_1m_shift', 'PMI_3m_shift', 
                'UNR_3m_shift', 'YUNR_3m_shift', 'CONS_SENT_3m_shift', 'CAP_UTIL_3m_shift',
                '3 Month Treasury Yield (Bond Equivalent Basis)_3m_shift',
                'UNR_12m_shift', 'CONS_SENT_12m_shift', 'HOUS_PERMS_12m_shift','HOUS_STARTS_12m_shift',
                '3YRT_12m_shift','10 Year Treasury Yield_12m_shift','Spread_12m_shift','PPI_1m_shift',
                'CPI_3m_shift','PPI_3m_shift','CPI_12m_shift','PPI_12m_shift']

dataset = dataset.drop(columns = splined_cols)

In [129]:
dataset = dataset.join(features, how='outer')

In [130]:
dataset.shape

(722, 165)

In [131]:
dataset[12:]

UNR  YUNR  PART_TIME  CPPR_PRICE   HOUS_PERMS  HOUS_STARTS  \
1960-01-01   5.3  11.1     1000.0  165.088781  1331.221607       1601.0   
1960-02-01   5.2  10.9     1015.0  165.088781  1092.000000       1460.0   
1960-03-01   4.8  10.2     1062.0  165.088781  1088.000000       1503.0   
1960-04-01   5.4  11.5      888.0  165.088781   955.000000       1109.0   
1960-05-01   5.2  10.9     1041.0  165.088781  1016.000000       1289.0   
1960-06-01   5.1  10.7      988.0  165.088781  1052.000000       1271.0   
1960-07-01   5.4  11.0      966.0  165.088781   958.000000       1247.0   
1960-08-01   5.5  10.8     1013.0  165.088781   999.000000       1197.0   
1960-09-01   5.6  11.4     1018.0  165.088781   994.000000       1344.0   
1960-10-01   5.5  11.0     1027.0  165.088781   984.000000       1097.0   
1960-11-01   6.1  11.8     1017.0  165.088781   972.000000       1246.0   
1960-12-01   6.1  12.0     1086.0  165.088781   979.000000       1246.0   
1961-01-01   6.6  13.0     1104.0  165.088781   951.000000       1063.0   
1961-02-01   6.6  13.0     1177.0  165.088781   969.000000       1183.0   
1961-03-01   6.9  13.3     1060.0  165.088781   961.000000       1226.0   
1961-04-01   6.9  13.4     1101.0  165.088781  1000.000000       1312.0   
1961-05-01   7.0  14.3     1140.0  165.088781  1002.000000       1166.0   
1961-06-01   7.1  13.1     1181.0  165.088781  1027.000000       1228.0   
1961-07-01   6.9  13.1     1215.0  165.088781  1070.000000       1382.0   
1961-08-01   7.0  13.4     1118.0  165.088781  1083.000000       1335.0   
1961-09-01   6.6  13.0     1185.0  165.088781  1159.000000       1312.0   
1961-10-01   6.7  13.1     1196.0  165.088781  1098.000000       1429.0   
1961-11-01   6.5  12.8     1101.0  165.088781  1123.000000       1415.0   
1961-12-01   6.1  12.0     1163.0  165.088781  1152.000000       1385.0   
1962-01-01   6.0  11.9     1036.0  165.088781  1161.000000       1365.0   
1962-02-01   5.8  12.0      976.0  165.088781  1122.000000       1361.0   
1962-03-01   5.5  11.6     1017.0  165.088781  1194.000000       1278.0   
1962-04-01   5.6  11.6     1044.0  165.088781  1134.000000       1443.0   
1962-05-01   5.6  11.2     1001.0  165.088781  1235.000000       1524.0   
1962-06-01   5.5  11.0     1044.0  165.088781  1142.000000       1483.0   
1962-07-01   5.5  10.5     1006.0  165.088781  1154.000000       1404.0   
1962-08-01   5.4  11.1     1025.0  165.088781  1189.000000       1450.0   
1962-09-01   5.7  11.9      898.0  165.088781  1200.000000       1517.0   
1962-10-01   5.6  11.3     1010.0  165.088781  1223.000000       1324.0   
1962-11-01   5.4  11.1     1076.0  165.088781  1181.000000       1533.0   
1962-12-01   5.7  11.9      982.0  165.088781  1236.000000       1622.0   
1963-01-01   5.5  11.1     1027.0  165.088781  1236.000000       1564.0   
1963-02-01   5.7  11.6      968.0  165.088781  1248.000000       1244.0   
1963-03-01   5.9  12.4      998.0  165.088781  1212.000000       1456.0   
1963-04-01   5.7  12.0     1001.0  165.088781  1258.000000       1534.0   
1963-05-01   5.7  12.0      959.0  165.088781  1288.000000       1689.0   
1963-06-01   5.9  12.7      961.0  165.088781  1350.000000       1641.0   
1963-07-01   5.6  12.2     1000.0  165.088781  1345.000000       1588.0   
1963-08-01   5.6  12.6      927.0  165.088781  1321.000000       1614.0   
1963-09-01   5.4  11.8      964.0  165.088781  1310.000000       1639.0   
1963-10-01   5.5  12.5      956.0  165.088781  1413.000000       1763.0   
1963-11-01   5.5  12.5      942.0  165.088781  1414.000000       1779.0   
1963-12-01   5.7  12.5      945.0  165.088781  1357.000000       1622.0   
1964-01-01   5.5  11.7      900.0  165.088781  1423.000000       1491.0   
1964-02-01   5.6  12.1      939.0  165.088781  1296.000000       1603.0   
1964-03-01   5.4  11.8      974.0  165.088781  1442.000000       1820.0   
1964-04-01   5.4  11.8      943.0  165.088781  1313.000000       1517.0   
1964-05-01   5.3  11.9      938.0  165

In [132]:
#cutoff most of missing data, Post March 2019, Prior 1959. CPI/PPI missing 2016 onward so need to cut that off
#dataset = dataset.iloc[552:]
#dataset = dataset.iloc[:-2]

#y = y.iloc[552:]
y = dataset['Recession']
dataset = dataset.drop(columns = ['Recession'])
X = dataset

In [133]:
### Data Prep Finished Here ###

In [134]:
y_shift = y.shift(0) #needs to be negative to look forward
y_shift = y_shift.fillna(0)

In [135]:
X_train = X.iloc[12:550]
X_test = X.iloc[550:]
y_train = y_shift.iloc[12:550]
y_test = y_shift.iloc[550:]

In [136]:
model = LogisticRegression(penalty = 'l2', C=2000, max_iter = 100, solver = 'sag') #try throwing in a bigger C than 1
#RidgeClassifier().fit(X, y)
model.fit(X_train, y_train) #fitting model

/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:334: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)


LogisticRegression(C=2000, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='warn',
          n_jobs=None, penalty='l2', random_state=None, solver='sag',
          tol=0.0001, verbose=0, warm_start=False)

In [137]:
probs = model.predict_proba(X_test)

In [138]:
y_test.shape

(172,)

In [139]:
X_test.shape

(172, 164)

In [140]:
log_loss(y_test, probs)

0.3183444415304694

In [141]:
roc_auc_score(y_test.values, probs[:,1:])

0.7953265765765766

In [142]:
results = pd.DataFrame(probs)
results['actual'] = y_test.values
results.index = y_test.index
pd.set_option('display.float_format', lambda x: '%.3f' % x)
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    print(results)

               0     1  actual
2004-11-01 0.932 0.068   0.000
2004-12-01 0.839 0.161   0.000
2005-01-01 0.976 0.024   0.000
2005-02-01 0.983 0.017   0.000
2005-03-01 0.964 0.036   0.000
2005-04-01 0.920 0.080   0.000
2005-05-01 0.951 0.049   0.000
2005-06-01 0.872 0.128   0.000
2005-07-01 0.981 0.019   0.000
2005-08-01 0.908 0.092   0.000
2005-09-01 0.974 0.026   0.000
2005-10-01 0.904 0.096   0.000
2005-11-01 0.947 0.053   0.000
2005-12-01 0.984 0.016   0.000
2006-01-01 0.991 0.009   0.000
2006-02-01 0.970 0.030   0.000
2006-03-01 0.970 0.030   0.000
2006-04-01 0.966 0.034   0.000
2006-05-01 0.877 0.123   0.000
2006-06-01 0.903 0.097   0.000
2006-07-01 0.798 0.202   0.000
2006-08-01 0.936 0.064   0.000
2006-09-01 0.826 0.174   0.000
2006-10-01 0.843 0.157   0.000
2006-11-01 0.856 0.144   0.000
2006-12-01 0.684 0.316   0.000
2007-01-01 0.599 0.401   0.000
2007-02-01 0.534 0.466   0.000
2007-03-01 0.842 0.158   0.000
2007-04-01 0.803 0.197   0.000
2007-05-01 0.737 0.263   0.000
2007-06-